# Assignment 5

This is the starter code for Assignment 5. In this assignment, you will solve increasingly challenging tasks from the [Minigrid benchmark](https://minigrid.farama.org/). You can use any RL algorithm to solve these tasks.

* Problems 1 and 2 are mandatory for all students.
* Problem 3 is mandatory for COMP 552 but optional for COMP 442.
* Problem 4 is optional for all.

In [ ]:
!pip install torch
!pip install gymnasium
!pip install minigrid

In [1]:
import gymnasium as gym
import minigrid
import numpy as np

np.set_printoptions(formatter={'float': lambda x: "{0:0.2f}".format(x)})

pygame 2.5.2 (SDL 2.28.3, Python 3.11.5)
Hello from the pygame community. https://www.pygame.org/contribute.html


In [2]:
def compute_score(task, policy):
  num_episodes = 10
  cur_episode  = 0

  seed_by_episode = [42, 34, 50, 1, 9, 7, 43, 56, 90, 11]
  score_by_episode = np.zeros(num_episodes)

  while cur_episode < num_episodes:

    cumulative_reward = 0
    cur_seed = seed_by_episode[cur_episode]

    observation, info = task.reset(seed=cur_seed)
    done = False

    while not done:
      action = policy(observation)
      observation, reward, terminated, truncated, info = task.step(action)
      cumulative_reward += reward

      if terminated or truncated:
        done = True
        score_by_episode[cur_episode] = cumulative_reward
        cur_episode += 1

  score_mean = round(score_by_episode.mean(), 3)
  score_std  = round(score_by_episode.std(), 3)
  score_best = round(score_by_episode.max(), 3)

  print(f"Best score: {score_best}")
  print(f"Average score: {score_mean, score_std}")

  return score_by_episode

## Problem 1
Solve the [Minigrid Unlock](https://minigrid.farama.org/environments/minigrid/UnlockEnv/) task.

This problem is worth 5 points.

![](https://minigrid.farama.org/_images/UnlockEnv.gif)

In [3]:
! python -m rl_zoo3.train --algo ppo --env MiniGrid-Unlock-v0

========== MiniGrid-Unlock-v0 ==========
Seed: 2577565073
Loading hyperparameters from: /opt/homebrew/anaconda3/lib/python3.11/site-packages/rl_zoo3/hyperparams/ppo.yml
Default hyperparameters for environment (ones being tuned will be overridden):
OrderedDict([('batch_size', 64),
             ('clip_range', 0.2),
             ('ent_coef', 0.0),
             ('env_wrapper', 'minigrid.wrappers.FlatObsWrapper'),
             ('gae_lambda', 0.95),
             ('gamma', 0.99),
             ('learning_rate', 0.00025),
             ('n_envs', 8),
             ('n_epochs', 10),
             ('n_steps', 128),
             ('n_timesteps', 100000.0),
             ('normalize', True),
             ('policy', 'MlpPolicy')])
Using 8 environments
Creating test environment
Normalization activated: {'gamma': 0.99, 'norm_reward': False, 'training': False}
Normalization activated: {'gamma': 0.99}
Using cpu device
Log path: logs/ppo/MiniGrid-Unlock-v0_1
-----------------------------
| time/              

In [10]:
from minigrid.wrappers import FlatObsWrapper
from stable_baselines3 import PPO

In [11]:
model = PPO.load("logs/ppo/MiniGrid-Unlock-v0_1/best_model.zip")

In [12]:


def first_policy(observation):
  ######## PUT YOUR CODE HERE ########
  action, _states = model.predict(observation)
  ######## PUT YOUR CODE HERE ########
  return action

In [14]:

first_task = gym.make("MiniGrid-Unlock-v0")
first_task = FlatObsWrapper(first_task)

compute_score(task=first_task, policy=first_policy)

Best score: 0.975
Average score: (0.804, 0.175)


array([0.97, 0.69, 0.76, 0.85, 0.35, 0.97, 0.91, 0.78, 0.83, 0.92])

### Discussion
I employed a PPO algorithm using RL zoo. The code is able to finish in about a minute, which is impressive. The reward is also able to climb past 0.8, which means the agent is able to quickly find the key and unlock the door.

## Problem 2
Solve the [Minigrid Unlock and Pickup](https://minigrid.farama.org/environments/minigrid/UnlockPickupEnv/) task.

This problem is worth 10 points for COMP 442 students.
This problem is worth 05 points for COMP 552 students.

![](https://minigrid.farama.org/_images/UnlockPickupEnv.gif)

In [240]:
! cd Minigrid-master/minigrid/ ; python3 manual_control.py --env MiniGrid-UnlockPickup-v0 > ~/Documents/documents-main/school/rice/fall_2023/comp_552/HW5/log.txt

78621.18s - pydevd: Sending message related to process being replaced timed-out after 5 seconds
Traceback (most recent call last):
  File "/Users/kmm12/Documents/documents-main/school/rice/fall_2023/comp_552/HW5/Minigrid-master/minigrid/manual_control.py", line 181, in <module>
    manual_control.start()
  File "/Users/kmm12/Documents/documents-main/school/rice/fall_2023/comp_552/HW5/Minigrid-master/minigrid/manual_control.py", line 39, in start
    for event in pygame.event.get():
                 ^^^^^^^^^^^^^^^^^^
pygame.error: video system not initialized


In [244]:
import pickle

pkl_file = open('traj_list_2.pkl', 'rb')

traj_list = pickle.load(pkl_file)

In [245]:
from imitation.data.rollout import flatten_trajectories as ft

trans_list = ft(traj_list)

In [257]:
import numpy as np
from imitation.policies.serialize import load_policy
from imitation.util.util import make_vec_env
from minigrid.wrappers import RGBImgPartialObsWrapper

SEED = 42

# second_task = gym.make("MiniGrid-UnlockPickup-v0")
# second_task = ImgObsWrapper(second_task)


# env = make_vec_env(
#     "MiniGrid-UnlockPickup-v0",
#     rng=np.random.default_rng(SEED),
#     n_envs=8)


second_task = make_vec_env(
    "MiniGrid-UnlockPickup-v0",
    rng=np.random.default_rng(SEED),
    n_envs=8,
    post_wrappers=[
        lambda env, _: FlatObsWrapper(env)
    ],  # needed for computing rollouts later
)

In [258]:
from imitation.algorithms.adversarial.gail import GAIL
from imitation.rewards.reward_nets import BasicRewardNet
from imitation.util.networks import RunningNorm
from stable_baselines3 import PPO
from stable_baselines3.ppo import MlpPolicy
from stable_baselines3.common.evaluation import evaluate_policy

learner = PPO(
    env=second_task,
    policy=MlpPolicy,
    batch_size=64,
    ent_coef=0.0,
    learning_rate=0.00025,
    gamma=0.99,
    n_epochs=10,
    clip_range=0.2,
    gae_lambda=0.95,
    seed=SEED,
)

reward_net = BasicRewardNet(
    observation_space=second_task.observation_space,
    action_space=second_task.action_space,
    normalize_input_layer=RunningNorm,
)

gail_trainer = GAIL(
    demonstrations=traj_list,
    demo_batch_size=1024,
    gen_replay_buffer_capacity=512,
    n_disc_updates_per_round=8,
    venv=second_task,
    gen_algo=learner,
    reward_net=reward_net,
    allow_variable_horizon=True
)

# evaluate the learner before training
second_task.seed(SEED)
learner_rewards_before_training, _ = evaluate_policy(
    learner, second_task, 100, return_episode_rewards=True
)

# train the learner and evaluate again
gail_trainer.train(1_000_000)


second_task.seed(SEED)
learner_rewards_after_training, _ = evaluate_policy(
    learner, second_task, 100, return_episode_rewards=True
)


Running with `allow_variable_horizon` set to True. Some algorithms are biased towards shorter or longer episodes, which may significantly confound results. Additionally, even unbiased algorithms can exploit the information leak from the termination condition, producing spuriously high performance. See https://imitation.readthedocs.io/en/latest/getting-started/variable-horizon.html for more information.


round:   0%|          | 0/61 [00:00<?, ?it/s]

------------------------------------------
| raw/                        |          |
|    gen/rollout/ep_len_mean  | 288      |
|    gen/rollout/ep_rew_mean  | 0        |
|    gen/time/fps             | 1894     |
|    gen/time/iterations      | 1        |
|    gen/time/time_elapsed    | 8        |
|    gen/time/total_timesteps | 16384    |
------------------------------------------
--------------------------------------------------
| raw/                                |          |
|    disc/disc_acc                    | 0.5      |
|    disc/disc_acc_expert             | 0        |
|    disc/disc_acc_gen                | 1        |
|    disc/disc_entropy                | 0.691    |
|    disc/disc_loss                   | 0.695    |
|    disc/disc_proportion_expert_pred | 0        |
|    disc/disc_proportion_expert_true | 0.5      |
|    disc/global_step                 | 1        |
|    disc/n_expert                    | 1.02e+03 |
|    disc/n_generated                 | 1.02e+03 |
-

round:   2%|▏         | 1/61 [00:17<17:59, 18.00s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 288         |
|    gen/rollout/ep_rew_mean         | 0           |
|    gen/rollout/ep_rew_wrapped_mean | 179         |
|    gen/time/fps                    | 1919        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 32768       |
|    gen/train/approx_kl             | 0.011278102 |
|    gen/train/clip_fraction         | 0.112       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -1.94       |
|    gen/train/explained_variance    | -0.0427     |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 0.787       |
|    gen/train/n_updates             | 10          |
|    gen/train/policy_gradient_loss  | -0.00702    |
|    gen/train/value_loss            | 3.8    

...

round:  97%|█████████▋| 59/61 [17:50<00:36, 18.07s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 282         |
|    gen/rollout/ep_rew_mean         | 0.0225      |
|    gen/rollout/ep_rew_wrapped_mean | 201         |
|    gen/time/fps                    | 1867        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 983040      |
|    gen/train/approx_kl             | 0.022635762 |
|    gen/train/clip_fraction         | 0.202       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.868      |
|    gen/train/explained_variance    | 0.965       |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 2.6         |
|    gen/train/n_updates             | 590         |
|    gen/train/policy_gradient_loss  | -0.0136     |
|    gen/train/value_loss            | 13.2   

round:  98%|█████████▊| 60/61 [18:08<00:18, 18.11s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 282         |
|    gen/rollout/ep_rew_mean         | 0.0237      |
|    gen/rollout/ep_rew_wrapped_mean | 193         |
|    gen/time/fps                    | 1897        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 999424      |
|    gen/train/approx_kl             | 0.018712664 |
|    gen/train/clip_fraction         | 0.176       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.903      |
|    gen/train/explained_variance    | 0.96        |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 3.36        |
|    gen/train/n_updates             | 600         |
|    gen/train/policy_gradient_loss  | -0.0123     |
|    gen/train/value_loss            | 8.93   

round: 100%|██████████| 61/61 [18:26<00:00, 18.14s/it]


In [261]:
def second_policy(observation):
  ######## PUT YOUR CODE HERE ########
  action, _states = learner.predict(observation)
  ######## PUT YOUR CODE HERE ########
  return action

In [262]:
env = gym.make("MiniGrid-UnlockPickup-v0")
env = FlatObsWrapper(env)

In [269]:
compute_score(task=env, policy=second_policy)

Best score: 0.531
Average score: (0.053, 0.159)


array([0.     , 0.     , 0.     , 0.     , 0.     , 0.     , 0.     ,
       0.     , 0.     , 0.53125])

In [270]:
gail_trainer.train(1_000_000)

round:   0%|          | 0/61 [00:00<?, ?it/s]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 287         |
|    gen/rollout/ep_rew_mean         | 0.00663     |
|    gen/rollout/ep_rew_wrapped_mean | 201         |
|    gen/time/fps                    | 1908        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 1015808     |
|    gen/train/approx_kl             | 0.020309025 |
|    gen/train/clip_fraction         | 0.179       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.889      |
|    gen/train/explained_variance    | 0.949       |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 3.58        |
|    gen/train/n_updates             | 610         |
|    gen/train/policy_gradient_loss  | -0.00932    |
|    gen/train/value_loss            | 12.4   

round:   2%|▏         | 1/61 [00:18<18:20, 18.34s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 285         |
|    gen/rollout/ep_rew_mean         | 0.0107      |
|    gen/rollout/ep_rew_wrapped_mean | 251         |
|    gen/time/fps                    | 1863        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 1032192     |
|    gen/train/approx_kl             | 0.021098066 |
|    gen/train/clip_fraction         | 0.183       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.945      |
|    gen/train/explained_variance    | 0.962       |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 2.12        |
|    gen/train/n_updates             | 620         |
|    gen/train/policy_gradient_loss  | -0.0132     |
|    gen/train/value_loss            | 11.4   

round:   3%|▎         | 2/61 [00:37<18:18, 18.62s/it]

...

round:  97%|█████████▋| 59/61 [19:05<00:38, 19.36s/it]

--------------------------------------------------
| raw/                               |           |
|    gen/rollout/ep_len_mean         | 280       |
|    gen/rollout/ep_rew_mean         | 0.0329    |
|    gen/rollout/ep_rew_wrapped_mean | 210       |
|    gen/time/fps                    | 1762      |
|    gen/time/iterations             | 1         |
|    gen/time/time_elapsed           | 9         |
|    gen/time/total_timesteps        | 1982464   |
|    gen/train/approx_kl             | 0.0212855 |
|    gen/train/clip_fraction         | 0.16      |
|    gen/train/clip_range            | 0.2       |
|    gen/train/entropy_loss          | -0.608    |
|    gen/train/explained_variance    | 0.852     |
|    gen/train/learning_rate         | 0.00025   |
|    gen/train/loss                  | 2.99      |
|    gen/train/n_updates             | 1200      |
|    gen/train/policy_gradient_loss  | -0.0127   |
|    gen/train/value_loss            | 19.6      |
-------------------------------

round:  98%|█████████▊| 60/61 [19:25<00:19, 19.43s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 270         |
|    gen/rollout/ep_rew_mean         | 0.0718      |
|    gen/rollout/ep_rew_wrapped_mean | 189         |
|    gen/time/fps                    | 1811        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 1998848     |
|    gen/train/approx_kl             | 0.039381087 |
|    gen/train/clip_fraction         | 0.191       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.663      |
|    gen/train/explained_variance    | 0.847       |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 1.98        |
|    gen/train/n_updates             | 1210        |
|    gen/train/policy_gradient_loss  | -0.0151     |
|    gen/train/value_loss            | 10.7   

round: 100%|██████████| 61/61 [19:44<00:00, 19.42s/it]


In [273]:
compute_score(task=env, policy=second_policy)

Best score: 0.638
Average score: (0.175, 0.268)


array([0.      , 0.      , 0.      , 0.      , 0.534375, 0.575   ,
       0.6375  , 0.      , 0.      , 0.      ])

In [274]:
gail_trainer.train(2_000_000)

round:   0%|          | 0/122 [00:00<?, ?it/s]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 271         |
|    gen/rollout/ep_rew_mean         | 0.0715      |
|    gen/rollout/ep_rew_wrapped_mean | 180         |
|    gen/time/fps                    | 1806        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 2015232     |
|    gen/train/approx_kl             | 0.026362428 |
|    gen/train/clip_fraction         | 0.169       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.681      |
|    gen/train/explained_variance    | 0.809       |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 2.99        |
|    gen/train/n_updates             | 1220        |
|    gen/train/policy_gradient_loss  | -0.0135     |
|    gen/train/value_loss            | 24     

round:   1%|          | 1/122 [00:20<41:46, 20.72s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 274         |
|    gen/rollout/ep_rew_mean         | 0.06        |
|    gen/rollout/ep_rew_wrapped_mean | 188         |
|    gen/time/fps                    | 1690        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 2031616     |
|    gen/train/approx_kl             | 0.032290228 |
|    gen/train/clip_fraction         | 0.207       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.737      |
|    gen/train/explained_variance    | 0.866       |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 7.48        |
|    gen/train/n_updates             | 1230        |
|    gen/train/policy_gradient_loss  | -0.0164     |
|    gen/train/value_loss            | 20.1   

round:   2%|▏         | 2/122 [00:41<41:33, 20.78s/it]

...

round:  98%|█████████▊| 120/122 [40:06<00:41, 20.51s/it]

---------------------------------------------------
| raw/                               |            |
|    gen/rollout/ep_len_mean         | 271        |
|    gen/rollout/ep_rew_mean         | 0.0703     |
|    gen/rollout/ep_rew_wrapped_mean | 182        |
|    gen/time/fps                    | 1767       |
|    gen/time/iterations             | 1          |
|    gen/time/time_elapsed           | 9          |
|    gen/time/total_timesteps        | 3981312    |
|    gen/train/approx_kl             | 0.02731313 |
|    gen/train/clip_fraction         | 0.189      |
|    gen/train/clip_range            | 0.2        |
|    gen/train/entropy_loss          | -0.568     |
|    gen/train/explained_variance    | 0.825      |
|    gen/train/learning_rate         | 0.00025    |
|    gen/train/loss                  | 4.99       |
|    gen/train/n_updates             | 2420       |
|    gen/train/policy_gradient_loss  | -0.0172    |
|    gen/train/value_loss            | 18.5       |
------------

round:  99%|█████████▉| 121/122 [40:25<00:20, 20.18s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 269         |
|    gen/rollout/ep_rew_mean         | 0.0759      |
|    gen/rollout/ep_rew_wrapped_mean | 183         |
|    gen/time/fps                    | 1778        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 3997696     |
|    gen/train/approx_kl             | 0.026008941 |
|    gen/train/clip_fraction         | 0.2         |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.597      |
|    gen/train/explained_variance    | 0.83        |
|    gen/train/learning_rate         | 0.00025     |
|    gen/train/loss                  | 6.11        |
|    gen/train/n_updates             | 2430        |
|    gen/train/policy_gradient_loss  | -0.0188     |
|    gen/train/value_loss            | 21.7   

round: 100%|██████████| 122/122 [40:45<00:00, 20.05s/it]


In [533]:
compute_score(task=env, policy=second_policy)

Best score: 0.875
Average score: (0.192, 0.309)


array([0.      , 0.      , 0.      , 0.875   , 0.      , 0.465625,
       0.584375, 0.      , 0.      , 0.      ])

### Discussion

I used GAIL to solve this problem. This required that I play the game and record it so that the agent could learn from me, the expert. The agent was able to get upt to about 0.2 average reward. It performs pretty well, unless it gets stuck and gets 0 reward. This happens a lot, and is the reason why the agent doesn't do better. I believe this is because of the limited number of expert runs I give to the agent. I believe with more time on my hands, I could play the game more, and the agent would do much better.

## Problem 3
Solve the [Minigrid Blocked, Unlock and Pickup](https://minigrid.farama.org/environments/minigrid/BlockedUnlockPickupEnv/) task.

This problem is optional for COMP 442 students.
This problem is mandatory for COMP 552 students.

This problem is worth 05 points for COMP 552 students.

![](https://minigrid.farama.org/_images/BlockedUnlockPickupEnv.gif)

In [581]:
! cd Minigrid-master/minigrid/ ; python3 manual_control.py --env MiniGrid-BlockedUnlockPickup-v0

100717.86s - pydevd: Sending message related to process being replaced timed-out after 5 seconds
down
down
Traceback (most recent call last):
  File "/Users/kmm12/Documents/documents-main/school/rice/fall_2023/comp_552/HW5/Minigrid-master/minigrid/manual_control.py", line 181, in <module>
    manual_control.start()
  File "/Users/kmm12/Documents/documents-main/school/rice/fall_2023/comp_552/HW5/Minigrid-master/minigrid/manual_control.py", line 39, in start
    for event in pygame.event.get():
                 ^^^^^^^^^^^^^^^^^^
pygame.error: video system not initialized


In [582]:
import pickle

pkl_file = open('traj_list.pkl', 'rb')

traj_list = pickle.load(pkl_file)

In [583]:
import numpy as np
from imitation.policies.serialize import load_policy
from imitation.util.util import make_vec_env
from minigrid.wrappers import RGBImgPartialObsWrapper

SEED = 42


third_task = make_vec_env(
    "MiniGrid-BlockedUnlockPickup-v0",
    rng=np.random.default_rng(SEED),
    n_envs=8,
    post_wrappers=[
        lambda env, _: FlatObsWrapper(env)
    ],  # needed for computing rollouts later
)

In [584]:

learner3 = PPO(
    env=third_task,
    policy=MlpPolicy,
    batch_size=64,
    ent_coef=0.0,
    learning_rate=0.0004,
    gamma=0.99,
    n_epochs=10,
    clip_range=0.2,
    gae_lambda=0.95,
    seed=SEED,
)

reward_net3 = BasicRewardNet(
    observation_space=third_task.observation_space,
    action_space=third_task.action_space,
    normalize_input_layer=RunningNorm,
)

gail_trainer3 = GAIL(
    demonstrations=traj_list,
    demo_batch_size=1024,
    gen_replay_buffer_capacity=512,
    n_disc_updates_per_round=8,
    venv=third_task,
    gen_algo=learner3,
    reward_net=reward_net3,
    allow_variable_horizon=True
)


# train the learner and evaluate again
gail_trainer3.train(1_000_000)




Running with `allow_variable_horizon` set to True. Some algorithms are biased towards shorter or longer episodes, which may significantly confound results. Additionally, even unbiased algorithms can exploit the information leak from the termination condition, producing spuriously high performance. See https://imitation.readthedocs.io/en/latest/getting-started/variable-horizon.html for more information.


round:   0%|          | 0/61 [00:00<?, ?it/s]

------------------------------------------
| raw/                        |          |
|    gen/rollout/ep_len_mean  | 576      |
|    gen/rollout/ep_rew_mean  | 0        |
|    gen/time/fps             | 1819     |
|    gen/time/iterations      | 1        |
|    gen/time/time_elapsed    | 9        |
|    gen/time/total_timesteps | 16384    |
------------------------------------------
--------------------------------------------------
| raw/                                |          |
|    disc/disc_acc                    | 0.5      |
|    disc/disc_acc_expert             | 0        |
|    disc/disc_acc_gen                | 1        |
|    disc/disc_entropy                | 0.691    |
|    disc/disc_loss                   | 0.696    |
|    disc/disc_proportion_expert_pred | 0        |
|    disc/disc_proportion_expert_true | 0.5      |
|    disc/global_step                 | 1        |
|    disc/n_expert                    | 1.02e+03 |
|    disc/n_generated                 | 1.02e+03 |
-

round:   2%|▏         | 1/61 [00:18<18:10, 18.18s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 575         |
|    gen/rollout/ep_rew_mean         | 0.00282     |
|    gen/rollout/ep_rew_wrapped_mean | 358         |
|    gen/time/fps                    | 1899        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 32768       |
|    gen/train/approx_kl             | 0.013002751 |
|    gen/train/clip_fraction         | 0.148       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -1.94       |
|    gen/train/explained_variance    | -0.0644     |
|    gen/train/learning_rate         | 0.0004      |
|    gen/train/loss                  | 0.685       |
|    gen/train/n_updates             | 10          |
|    gen/train/policy_gradient_loss  | -0.00793    |
|    gen/train/value_loss            | 2.16   

...

round:  97%|█████████▋| 59/61 [18:57<00:39, 19.80s/it]

---------------------------------------------------
| raw/                               |            |
|    gen/rollout/ep_len_mean         | 576        |
|    gen/rollout/ep_rew_mean         | 0          |
|    gen/rollout/ep_rew_wrapped_mean | 541        |
|    gen/time/fps                    | 1757       |
|    gen/time/iterations             | 1          |
|    gen/time/time_elapsed           | 9          |
|    gen/time/total_timesteps        | 983040     |
|    gen/train/approx_kl             | 0.01538196 |
|    gen/train/clip_fraction         | 0.145      |
|    gen/train/clip_range            | 0.2        |
|    gen/train/entropy_loss          | -1.05      |
|    gen/train/explained_variance    | 0.868      |
|    gen/train/learning_rate         | 0.0004     |
|    gen/train/loss                  | 81.5       |
|    gen/train/n_updates             | 590        |
|    gen/train/policy_gradient_loss  | -0.0108    |
|    gen/train/value_loss            | 184        |
------------

round:  98%|█████████▊| 60/61 [19:17<00:19, 19.76s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 576         |
|    gen/rollout/ep_rew_mean         | 0           |
|    gen/rollout/ep_rew_wrapped_mean | 447         |
|    gen/time/fps                    | 1812        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 999424      |
|    gen/train/approx_kl             | 0.020091439 |
|    gen/train/clip_fraction         | 0.18        |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -1.07       |
|    gen/train/explained_variance    | 0.887       |
|    gen/train/learning_rate         | 0.0004      |
|    gen/train/loss                  | 60.8        |
|    gen/train/n_updates             | 600         |
|    gen/train/policy_gradient_loss  | -0.0118     |
|    gen/train/value_loss            | 162    

round: 100%|██████████| 61/61 [19:36<00:00, 19.29s/it]


In [585]:
def third_policy(observation):
  ######## PUT YOUR CODE HERE ########
  action, _states = learner3.predict(observation)
  ######## PUT YOUR CODE HERE ########
  return action

In [586]:
env = gym.make("MiniGrid-BlockedUnlockPickup-v0")
env = FlatObsWrapper(env)

In [594]:
compute_score(task=env, policy=third_policy)

Best score: 0.2
Average score: (0.02, 0.06)


array([0. , 0.2, 0. , 0. , 0. , 0. , 0. , 0. , 0. , 0. ])

### Nice :)

In [595]:
gail_trainer3.train(5_000_000)

round:   0%|          | 0/305 [00:00<?, ?it/s]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 576         |
|    gen/rollout/ep_rew_mean         | 0           |
|    gen/rollout/ep_rew_wrapped_mean | 382         |
|    gen/time/fps                    | 1890        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 8           |
|    gen/time/total_timesteps        | 1015808     |
|    gen/train/approx_kl             | 0.021985818 |
|    gen/train/clip_fraction         | 0.241       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -1.11       |
|    gen/train/explained_variance    | 0.854       |
|    gen/train/learning_rate         | 0.0004      |
|    gen/train/loss                  | 2.89        |
|    gen/train/n_updates             | 610         |
|    gen/train/policy_gradient_loss  | -0.0143     |
|    gen/train/value_loss            | 18.1   

round:   0%|          | 1/305 [00:18<1:33:26, 18.44s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 571         |
|    gen/rollout/ep_rew_mean         | 0.0102      |
|    gen/rollout/ep_rew_wrapped_mean | 356         |
|    gen/time/fps                    | 1812        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 1032192     |
|    gen/train/approx_kl             | 0.020275325 |
|    gen/train/clip_fraction         | 0.203       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -1.14       |
|    gen/train/explained_variance    | 0.871       |
|    gen/train/learning_rate         | 0.0004      |
|    gen/train/loss                  | 2.25        |
|    gen/train/n_updates             | 620         |
|    gen/train/policy_gradient_loss  | -0.0133     |
|    gen/train/value_loss            | 30.1   

round:   1%|          | 2/305 [00:38<1:36:41, 19.15s/it]

...

round:  99%|█████████▉| 303/305 [1:36:48<00:40, 20.36s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 561         |
|    gen/rollout/ep_rew_mean         | 0.0315      |
|    gen/rollout/ep_rew_wrapped_mean | 406         |
|    gen/time/fps                    | 1786        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 5980160     |
|    gen/train/approx_kl             | 0.038816538 |
|    gen/train/clip_fraction         | 0.216       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.57       |
|    gen/train/explained_variance    | 0.822       |
|    gen/train/learning_rate         | 0.0004      |
|    gen/train/loss                  | 1.2         |
|    gen/train/n_updates             | 3640        |
|    gen/train/policy_gradient_loss  | -0.0136     |
|    gen/train/value_loss            | 16.8   

round: 100%|█████████▉| 304/305 [1:37:07<00:20, 20.09s/it]

----------------------------------------------------
| raw/                               |             |
|    gen/rollout/ep_len_mean         | 559         |
|    gen/rollout/ep_rew_mean         | 0.035       |
|    gen/rollout/ep_rew_wrapped_mean | 487         |
|    gen/time/fps                    | 1799        |
|    gen/time/iterations             | 1           |
|    gen/time/time_elapsed           | 9           |
|    gen/time/total_timesteps        | 5996544     |
|    gen/train/approx_kl             | 0.026088633 |
|    gen/train/clip_fraction         | 0.158       |
|    gen/train/clip_range            | 0.2         |
|    gen/train/entropy_loss          | -0.522      |
|    gen/train/explained_variance    | 0.867       |
|    gen/train/learning_rate         | 0.0004      |
|    gen/train/loss                  | 26.8        |
|    gen/train/n_updates             | 3650        |
|    gen/train/policy_gradient_loss  | -0.0118     |
|    gen/train/value_loss            | 56.8   

round: 100%|██████████| 305/305 [1:37:27<00:00, 19.17s/it]


In [702]:
compute_score(task=env, policy=third_policy)

Best score: 0.733
Average score: (0.136, 0.273)


array([0.7328125, 0.       , 0.       , 0.       , 0.       , 0.       ,
       0.628125 , 0.       , 0.       , 0.       ])

### Discussion
My thoughts are mainly the same as the last question. However, I know realize I probably made a mistake by using the FlatObsWrapper, which encodes the string instructions as part of the observations. In our use case, these don't matter as there is only ever one box of interest. Similarly, the color information does not matter. Thus, I believe I could get better performance with the ImgObsWrapper.

## Problem 4
This is a bonus problem and optional for all.

In this problem, the goal is to learn a unified agent for all the three tasks shown above.

In [ ]:
######## PUT YOUR CODE HERE ########
# Train an agent to solve the task

######## PUT YOUR CODE HERE ########

In [ ]:
def unified_policy(observation):
  ######## PUT YOUR CODE HERE ########
  action = first_task.action_space.sample()
  ######## PUT YOUR CODE HERE ########
  return action

In [ ]:
performance_on_first_task = compute_score(task=first_task, policy=unified_policy)

In [ ]:
performance_on_second_task = compute_score(task=second_task, policy=unified_policy)

In [ ]:
performance_on_third_task = compute_score(task=third_task, policy=unified_policy)

In [ ]:
total_performance = np.concatenate((performance_on_first_task, performance_on_second_task, performance_on_third_task), axis=None)

In [ ]:
print(f"Average score: {round(total_performance.mean(),3)}")